# Solving the Poisson Equation with NGSolve

This lecture is based on the NGSolve tutorial [...] For all details, documentation and the software please consult the webpage [...] 

We thank the developers and maintainers of NGSolve for making this software freely available for teaching and research.


# 1.1 The most simple example. 

We solve the Poisson problem with homogeneous Dirichlet data $u=0$ and the right hand side $f=1$ on a square domain $\Omega = (0,1)^2$

$$
\begin{aligned}
-\Delta u & = 1 && \text { in  the unit square},
\\
u & = 0 && \text{ on the boundary},
\end{aligned}
$$

## The preamble of NGSolve

#### 1. Import NGSolve and Netgen Python modules:

In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw

#### Problems? 

See the webpage https://ngsolve.org for install instructions

## Defining the domain and the finite element space

#### 2. Define the mesh

Simple geometries are part of NGSolve. The approximate mesh size $h$ (here $h=0.2$) is given as parameter

In [ ]:
mesh = Mesh(unit_square.GenerateMesh(maxh=0.2))
print('{} vertices and {} elements'.format(mesh.nv, mesh.ne)) # number of vertices & elements 

The mesh can be visualized

In [ ]:
Draw(mesh);

## --> Task

Modify the mesh size and visualize the mesh. Check how the number of vertices and elements grows if the mesh size is reduced. Try to verify the relation 
$$
N \approx \frac{1}{h^2}
$$



#### 3. Declare a finite element space:

Here, we want $H^1$-conforming finite element of order 2, so quadratic finite elements.

The boundary of the square has names and we must specify, where Dirichlet values are given.

In [ ]:
fes = H1(mesh, order=2, dirichlet="left|top|bottom|right")
print('The finite element space has {} degrees of freedom'.format(fes.ndof)) # number of unknowns in this space

## --> Task

Reduce the order to 1 (linear finite elements). What is the relation between degrees of freedom, number of vertices and number of elements? 

How does the number of degrees of freedom depend on the order?

#### 4. Declare test function, trial function, and grid function 

* Test and trial function are symbolic objects - called `ProxyFunctions` -  that help you construct bilinear forms. They do not really store data. They know, how to interprete the mesh. 

* `GridFunctions`, on the other hand, represent functions in the finite element space and contains memory to hold coefficient vectors. The grid function stores the coefficients $\alpha_1,\dots,\alpha_N$ of the basis representation

$$
u_h(x) = \sum_{i=1}^N \alpha_i \phi_h^{(i)}(x)
$$

In [ ]:
u = fes.TrialFunction()  # symbolic object
v = fes.TestFunction()   # symbolic object
gu = GridFunction(fes)   # solution is stored in an object calles GridFunction

# A short way to get trial and test functions at the same time is
# u,v = fes.TnT()

#### 5. Define and assemble linear and bilinear forms:

NGSolve is close to mathematics. The BilinearForm represents the variational form of Laplace
$$
(\nabla u,\nabla v)
$$

Likewise, the LinearForm represents the right hand side in variational formulation. 
$$
(f,v)
$$
and here, with $f=1$ it is
$$
(1,v)
$$

In [ ]:
a = BilinearForm(fes)     # construct the empty bilinear form
a += grad(u)*grad(v)*dx   # add the integral of laplace (dx stands for integration)
a.Assemble()              # Assemble the matrix

f = LinearForm(fes)       # construct the empty linear form for the right hand side
f += 1.0*v*dx             # add the integral for the right hand side f=1
f.Assemble();

We can print right hand side vector and matrix. But be careful, if the mesh is very large or the finite element order is high. 

In [ ]:
print(f.vec)

In [ ]:
print(a.mat)

#### 6. Solve the system:

Solving the linear systems can be delicate if the problem gets very large or complicated. Here, we only consider simple problems in 2d. As solver we always use an LU decomposition of the matrix. This is done by the following lines

In [ ]:
gu.vec.data = a.mat.Inverse(freedofs=fes.FreeDofs()) * f.vec

The Dirichlet boundary condition constrains some degrees of freedom. The argument `fes.FreeDofs()` indicates that only the remaining "free" degrees of freedom should participate in the linear solve.

We can print the solution

In [ ]:
print(gu.vec)

and, more important, we can visualize it

In [ ]:
Draw(gu)

## Summary

We conclude by presenting the complete code as one script

In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw

# Generate a mesh of the unit square
mesh = Mesh(unit_square.GenerateMesh(maxh=0.2))

# Define the finite element space. Here, linear
fes = H1(mesh, order=1, dirichlet="left|top|bottom|right")

u = fes.TrialFunction()  # symbolic object
v = fes.TestFunction()   # symbolic object
gu = GridFunction(fes)  # solution

a = BilinearForm(fes)     # construct the empty bilinear form
a += grad(u)*grad(v)*dx   # add the integral of laplace (dx stands for integration)
a.Assemble()              # Assemble the matrix

f = LinearForm(fes)       # construct the empty linear form for the right hand side
f += 1.0*v*dx             # add the integral for the right hand side f=1
f.Assemble();

gu.vec.data = a.mat.Inverse(freedofs=fes.FreeDofs()) * f.vec

Draw(gu)

### --> Task

Experiment with the script:

- What happens, if you do not specify all boundaries as Dirichlet? Can you interprete the result?
- Change the right hand side from $f=1$ to $f=xy$ or another function. You can directly use $x$ and $y$ to access the coordinates 

## Dirichlet boundary values

If we want to solve the Laplace equation with non-homogenous Dirichlet values, i.e.
$$
-\Delta u = f\text{ in } \Omega,\quad u=g\text{ on }\partial\Omega
$$
for a function $g:\partial\Omega\to\mathbb{R}$ we preceed like in the analysis of the Poisson problem:

1) We define a function $u_D\in H^1(\Omega)$ that is an extension of the Dirichlet data, i.e. $u_D=g$ on $\partial\Omega$.
2) We compute the residual $r=f - (-\Delta u_D)$ as new right hand side of the problem
3) We solve the homogeneous equation $-\Delta u_0 = r$
4) Compute the solution $u=u_D+u_0$

#### 1) Defining the boundary function

As example we solve
$$
-\Delta u = xy\text{ in }\Omega,\quad u = \sqrt{x+y}\text{ on }\partial\Omega
$$

In [ ]:
g = sqrt(x+y)           # The CoefficientFunction defining the boundary data
guD = GridFunction(fes)  # A finite element function on the mesh to store uD
guD.Set(g, BND)          # Interpolation of uD to the finite element space

Draw(guD);               # we can visualize it

#### 2) Compute the residual

In [ ]:
f = LinearForm(x*y*v*dx).Assemble()  # compute the right hand side (f,v)
r = f.vec - a.mat * guD.vec           # compute the residual

#### 3) Solve the homogeneous problem

In [ ]:
gu0 = GridFunction(fes)  # solution
gu0.vec.data = a.mat.Inverse(freedofs=fes.FreeDofs()) * r  # Solve -Delta u0 = r

Draw(gu0)

#### 4) Update the solution

In [ ]:
gu.vec.data = gu0.vec.data+guD.vec.data   # Add homogeneous solution and boundary extension
Draw(gu)  

## Summary

As summary and starting point for the next session we implement the problem
$$
-\Delta u(x,y) = 4cos(x)sin(y)\text{ in }\Omega,\quad u(x,y) = cos(x)sin(y)\text{ on }\partial\Omega
$$
The exact solution is $u(x,y) = cos(x)sin(y)$

In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw

mesh = Mesh(unit_square.GenerateMesh(maxh=0.1)) # unit square mesh

# quadratic FE
fes = H1(mesh, order=2, dirichlet="left|top|bottom|right")

u  = fes.TrialFunction()  # symbolic object
v  = fes.TestFunction()   # symbolic object
gu  = GridFunction(fes)    # solution
gu0 = GridFunction(fes)    # solution of homogeneous problem
guD = GridFunction(fes)    # extension of Dirichlet data

F = 2*cos(x)*sin(y)       # the right hand side function
g =   cos(x)*sin(y)       # Dirichlet Data
guD.Set(g,BND)            # interpolate to GridFunction

A = BilinearForm(grad(u)*grad(v)*dx).Assemble() # Compute Matrix

f = LinearForm(F*v*dx).Assemble() # construct right hand side
r = f.vec - A.mat * guD.vec       # compute the residual

gu0.vec.data = A.mat.Inverse(freedofs=fes.FreeDofs()) * r  # Solve homogeneous problem

gu.vec.data = gu0.vec.data+guD.vec.data  # update

Draw(gu) # plot

Draw(gu - cos(x)*sin(y),mesh) # plot the error
